In [1]:
import json

import bz2
import regex
from tqdm import tqdm
from scipy import sparse

In [2]:
import pandas as pd
import numpy as np
import nltk
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
%pylab inline

Populating the interactive namespace from numpy and matplotlib


In [3]:
responses = []
with bz2.BZ2File('banki_responses.json.bz2', 'r') as thefile:
    for row in tqdm(thefile):
        resp = json.loads(row)
        if not resp['rating_not_checked'] and (len(resp['text'].split()) > 0):
            responses.append(resp)

201030it [01:44, 1918.98it/s]


#  Домашнее задание по NLP # 1 [100 баллов]
## Классификация по тональности 

В этом домашнем задании вам предстоит классифицировать по тональности отзывы на банки с сайта banki.ru.

Данные содержат непосредственно тексты отзывов, некоторую дополнительную информацию, а также оценку по шкале от 1 до 5. 

Тексты хранятся в json-ах в массиве responses.

Посмотрим на пример отзыва:

## Часть 1. Анализ текстов [40/100]

### 1. Посчитайте количество отзывов в разных городах и на разные банки

In [ ]:
banks={}
cities={}
for i in range(0,len(responses)):
    if responses[i].get('bank_name') in banks.keys():
        banks[responses[i].get('bank_name')]+=1
    else:
        banks[responses[i].get('bank_name')]=1
    if responses[i].get('city') in cities.keys():
        cities[responses[i].get('city')]+=1
    else:
        cities[responses[i].get('city')]=1
banks = sorted(banks.items(), key=lambda kv: kv[1],reverse=True)
cities= sorted(cities.items(), key=lambda kv: kv[1],reverse=True)

In [ ]:
banks[:5]

In [ ]:
cities[:5]

### 2. Постройте гистограмы длин слов в символах и в словах

In [4]:
import re
regex = re.compile("[А-Яа-я]+")

def words_only(text, regex=regex):
    try:
        return " ".join(regex.findall(text))
    except:
        return ""

In [ ]:
reviews_symb = []
reviews_word = []
for i in tqdm(range(0,len(responses))):
    reviews_symb.append(len(responses[i].get('text')))
    reviews_word.append(len(words_only(responses[i].get('text')).split(' ')))

In [ ]:
plt.hist(reviews_symb);
plt.title("Гистограммма по кол-ву символов в отзыве");
plt.xlabel("Кол-во символов в отзыве");

In [ ]:
plt.hist(reviews_word);
plt.title("Гистограммма по кол-ву слов в отзыве");
plt.xlabel("Кол-во слов в отзыве");

### 3. Найдите 10 самых частых:
  * слов
  * слов без стоп-слов
  * лемм 
  * существительных


In [22]:
from collections import Counter

In [5]:
reviews_df = pd.DataFrame(responses)

In [6]:
reviews_df.head()

author     bank_license        bank_name            city  \
0       uhnov1  лицензия № 2562          Бинбанк       г. Москва   
1       Foryou  лицензия № 1481  Сбербанк России  г. Новосибирск   
2   Vladimir84  лицензия № 2562          Бинбанк       г. Москва   
3       643609  лицензия № 1481  Сбербанк России   г. Ставрополь   
4  anfisa-2003  лицензия № 2766         ОТП Банк    г. Челябинск   

              datetime  num_comments  rating_grade  rating_not_checked  \
0  2015-06-08 12:50:54             0           NaN               False   
1  2015-06-08 11:09:57             0           NaN               False   
2  2015-06-05 20:14:28             1           NaN               False   
3  2015-06-05 13:51:01             2           NaN               False   
4  2015-06-05 10:58:12             1           NaN               False   

                                                text  \
0  Добрый день! Я не являюсь клиентом банка и пор...   
1  Доброго дня! Являюсь держателем зарплатной кар...   
2  Здравствуйте!  Дублирую свое заявление от 03.0...   
3  Добрый день!! Я открыл расчетный счет в СберБа...   
4  04.03.2015 г. взяла кредит в вашем банке, заяв...   

                                               title  
0                                             Жалоба  
1      Не могу пользоваться услугой Сбербанк он-лайн  
2                    Двойное списание за один товар.  
3  Меняют проценты комиссии  не предупредив и не ...  
4             Верните денежные средства за страховку

In [7]:
reviews_df['text']=reviews_df.text.str.lower().apply(words_only)

In [8]:
reviews_df.head()

author     bank_license        bank_name            city  \
0       uhnov1  лицензия № 2562          Бинбанк       г. Москва   
1       Foryou  лицензия № 1481  Сбербанк России  г. Новосибирск   
2   Vladimir84  лицензия № 2562          Бинбанк       г. Москва   
3       643609  лицензия № 1481  Сбербанк России   г. Ставрополь   
4  anfisa-2003  лицензия № 2766         ОТП Банк    г. Челябинск   

              datetime  num_comments  rating_grade  rating_not_checked  \
0  2015-06-08 12:50:54             0           NaN               False   
1  2015-06-08 11:09:57             0           NaN               False   
2  2015-06-05 20:14:28             1           NaN               False   
3  2015-06-05 13:51:01             2           NaN               False   
4  2015-06-05 10:58:12             1           NaN               False   

                                                text  \
0  добрый день я не являюсь клиентом банка и пору...   
1  доброго дня являюсь держателем зарплатной карт...   
2  здравствуйте дублирую свое заявление от в до м...   
3  добрый день я открыл расчетный счет в сбербанк...   
4  г взяла кредит в вашем банке заявленная мною с...   

                                               title  
0                                             Жалоба  
1      Не могу пользоваться услугой Сбербанк он-лайн  
2                    Двойное списание за один товар.  
3  Меняют проценты комиссии  не предупредив и не ...  
4             Верните денежные средства за страховку

In [53]:
def the_most_common_words(df):
    cnt = Counter()
    tokens = []
    tokens = df.text.apply(lambda row: cnt.update(row.split(' ')))
    return cnt     

In [9]:
for i in the_most_common_words(reviews_df).most_common(10):
    print(i)

('в', 1330550)
('и', 1058997)
('не', 855335)
('на', 707935)
('что', 640057)
('я', 577500)
('с', 464037)
('по', 372769)
('мне', 320958)
('банка', 275906)


In [9]:
from nltk.corpus import stopwords
mystopwords = stopwords.words('russian')

In [10]:
def  remove_stopwords(text, mystopwords = mystopwords):
    try:
        return " ".join([token for token in text.split() if not token in mystopwords])
    except:
        return "" 

In [11]:
reviews_df['text']=reviews_df.text.apply(remove_stopwords)

In [12]:
reviews_df.head()

author     bank_license        bank_name            city  \
0       uhnov1  лицензия № 2562          Бинбанк       г. Москва   
1       Foryou  лицензия № 1481  Сбербанк России  г. Новосибирск   
2   Vladimir84  лицензия № 2562          Бинбанк       г. Москва   
3       643609  лицензия № 1481  Сбербанк России   г. Ставрополь   
4  anfisa-2003  лицензия № 2766         ОТП Банк    г. Челябинск   

              datetime  num_comments  rating_grade  rating_not_checked  \
0  2015-06-08 12:50:54             0           NaN               False   
1  2015-06-08 11:09:57             0           NaN               False   
2  2015-06-05 20:14:28             1           NaN               False   
3  2015-06-05 13:51:01             2           NaN               False   
4  2015-06-05 10:58:12             1           NaN               False   

                                                text  \
0  добрый день являюсь клиентом банка поручителем...   
1  доброго дня являюсь держателем зарплатной карт...   
2  здравствуйте дублирую свое заявление можайский...   
3  добрый день открыл расчетный счет сбербанке юр...   
4  г взяла кредит вашем банке заявленная мною сум...   

                                               title  
0                                             Жалоба  
1      Не могу пользоваться услугой Сбербанк он-лайн  
2                    Двойное списание за один товар.  
3  Меняют проценты комиссии  не предупредив и не ...  
4             Верните денежные средства за страховку

In [13]:
for i in the_most_common_words(reviews_df).most_common(10):
    print(i)

('банка', 275906)
('банк', 215426)
('это', 183365)
('деньги', 131201)
('карту', 105829)
('карты', 101821)
('т', 91756)
('кредит', 81136)
('день', 76552)
('банке', 72169)


In [13]:
from pymorphy2 import MorphAnalyzer
pm2 = MorphAnalyzer()

In [15]:
tqdm.pandas()

In [14]:
def def_lemm(text):
    try:        
        lemmas1 = [pm2.parse(word)[0].normal_form for word in text.split()]        
        return " ".join(lemmas1) 
    except:
        return " "

def lemmatize(df):
    df['text']=df.text.progress_apply(def_lemm)
    return df
    

In [16]:
reviews_df = lemmatize(reviews_df)

100%|██████████| 153499/153499 [1:24:22<00:00, 30.32it/s]  


In [17]:
reviews_df.head()

author     bank_license        bank_name            city  \
0       uhnov1  лицензия № 2562          Бинбанк       г. Москва   
1       Foryou  лицензия № 1481  Сбербанк России  г. Новосибирск   
2   Vladimir84  лицензия № 2562          Бинбанк       г. Москва   
3       643609  лицензия № 1481  Сбербанк России   г. Ставрополь   
4  anfisa-2003  лицензия № 2766         ОТП Банк    г. Челябинск   

              datetime  num_comments  rating_grade  rating_not_checked  \
0  2015-06-08 12:50:54             0           NaN               False   
1  2015-06-08 11:09:57             0           NaN               False   
2  2015-06-05 20:14:28             1           NaN               False   
3  2015-06-05 13:51:01             2           NaN               False   
4  2015-06-05 10:58:12             1           NaN               False   

                                                text  \
0  добрый день являться клиент банка поручитель к...   
1  добрый день являться держатель зарплатный карт...   
2  здравствовать дублировать свой заявление можай...   
3  добрый день открыть расчётный счёт сбербанк юр...   
4  год взять кредит ваш банка заявить я сумма том...   

                                               title  
0                                             Жалоба  
1      Не могу пользоваться услугой Сбербанк он-лайн  
2                    Двойное списание за один товар.  
3  Меняют проценты комиссии  не предупредив и не ...  
4             Верните денежные средства за страховку

In [18]:
reviews_df.to_csv('after_lemma.csv')

In [57]:
cnt = Counter()
tokens = []
tokens = reviews_df.text_noun.apply(lambda row: cnt.update(row.split(' ')))
for i in cnt.most_common(10):
    print(i)

('банка', 399725)
('карта', 334999)
('банк', 268864)
('деньга', 179819)
('день', 170152)
('год', 169247)
('кредит', 156177)
('отделение', 144050)
('клиент', 136893)
('сотрудник', 134168)


Скорее всего нужно добавить некторые слова в стоп-слова.

In [41]:
def find_noun(text):
    noun = []
    for w in text.split(' '):
        p = pm2.parse(w)[0].tag
        if {'NOUN'} in pm2.parse(w)[0].tag: 
            noun.append(w)
    return " ".join(noun)   

In [45]:
reviews_df['text_noun']=reviews_df.text.progress_apply(find_noun)



  0%|          | 0/153499 [00:00<?, ?it/s]

  0%|          | 3/153499 [00:00<1:34:39, 27.03it/s]

  0%|          | 6/153499 [00:00<1:38:14, 26.04it/s]

  0%|          | 10/153499 [00:00<1:28:54, 28.77it/s]

  0%|          | 13/153499 [00:00<2:30:45, 16.97it/s]

  0%|          | 16/153499 [00:00<2:22:21, 17.97it/s]

  0%|          | 20/153499 [00:01<2:14:11, 19.06it/s]

  0%|          | 22/153499 [00:01<2:39:09, 16.07it/s]

  0%|          | 24/153499 [00:01<2:59:19, 14.26it/s]

  0%|          | 31/153499 [00:01<2:17:08, 18.65it/s]

  0%|          | 35/153499 [00:01<2:37:34, 16.23it/s]

  0%|          | 38/153499 [00:01<2:25:51, 17.54it/s]

  0%|          | 41/153499 [00:02<2:19:26, 18.34it/s]

  0%|          | 44/153499 [00:02<2:13:40, 19.13it/s]

  0%|          | 47/153499 [00:02<2:00:56, 21.15it/s]

  0%|          | 50/153499 [00:02<2:09:55, 19.68it/s]

  0%|          | 53/153499 [00:02<2:07:46, 20.02it/s]

  0%|          | 56/153499 [00:02<1:57:34, 21.75it/s]

  0%|          | 60/1

  0%|          | 474/153499 [00:24<3:03:24, 13.91it/s]

  0%|          | 477/153499 [00:24<2:55:18, 14.55it/s]

  0%|          | 480/153499 [00:24<2:40:12, 15.92it/s]

  0%|          | 482/153499 [00:25<2:36:31, 16.29it/s]

  0%|          | 485/153499 [00:25<2:15:19, 18.85it/s]

  0%|          | 489/153499 [00:25<1:58:37, 21.50it/s]

  0%|          | 492/153499 [00:25<2:02:18, 20.85it/s]

  0%|          | 496/153499 [00:25<1:47:02, 23.82it/s]

  0%|          | 499/153499 [00:25<1:59:48, 21.28it/s]

  0%|          | 502/153499 [00:26<3:45:54, 11.29it/s]

  0%|          | 507/153499 [00:26<2:59:42, 14.19it/s]

  0%|          | 510/153499 [00:26<2:42:45, 15.67it/s]

  0%|          | 513/153499 [00:26<2:19:41, 18.25it/s]

  0%|          | 517/153499 [00:26<2:08:34, 19.83it/s]

  0%|          | 520/153499 [00:27<2:21:30, 18.02it/s]

  0%|          | 523/153499 [00:27<2:28:00, 17.23it/s]

  0%|          | 525/153499 [00:27<2:35:36, 16.38it/s]

  0%|          | 527/153499 [00:27<2:35:58, 16.3

  1%|          | 910/153499 [00:48<2:41:26, 15.75it/s]

  1%|          | 913/153499 [00:48<3:22:01, 12.59it/s]

  1%|          | 915/153499 [00:49<3:15:12, 13.03it/s]

  1%|          | 919/153499 [00:49<2:56:18, 14.42it/s]

  1%|          | 921/153499 [00:49<2:46:08, 15.31it/s]

  1%|          | 925/153499 [00:49<2:31:57, 16.73it/s]

  1%|          | 933/153499 [00:49<1:58:17, 21.50it/s]

  1%|          | 937/153499 [00:49<1:53:18, 22.44it/s]

  1%|          | 941/153499 [00:50<2:11:22, 19.35it/s]

  1%|          | 944/153499 [00:50<1:58:55, 21.38it/s]

  1%|          | 949/153499 [00:50<1:40:28, 25.30it/s]

  1%|          | 953/153499 [00:50<1:55:20, 22.04it/s]

  1%|          | 956/153499 [00:50<1:55:03, 22.10it/s]

  1%|          | 959/153499 [00:50<2:24:36, 17.58it/s]

  1%|          | 962/153499 [00:51<2:11:13, 19.37it/s]

  1%|          | 965/153499 [00:51<2:16:05, 18.68it/s]

  1%|          | 968/153499 [00:51<2:18:44, 18.32it/s]

  1%|          | 971/153499 [00:51<2:14:44, 18.8

  1%|          | 1343/153499 [01:13<2:27:34, 17.18it/s]

  1%|          | 1345/153499 [01:13<2:32:22, 16.64it/s]

  1%|          | 1348/153499 [01:14<3:11:52, 13.22it/s]

  1%|          | 1352/153499 [01:14<2:35:25, 16.32it/s]

  1%|          | 1355/153499 [01:14<2:14:24, 18.87it/s]

  1%|          | 1358/153499 [01:14<2:20:13, 18.08it/s]

  1%|          | 1361/153499 [01:14<2:33:26, 16.53it/s]

  1%|          | 1363/153499 [01:14<2:33:25, 16.53it/s]

  1%|          | 1366/153499 [01:15<2:32:47, 16.60it/s]

  1%|          | 1368/153499 [01:15<2:56:33, 14.36it/s]

  1%|          | 1370/153499 [01:15<3:00:15, 14.07it/s]

  1%|          | 1375/153499 [01:15<2:29:27, 16.96it/s]

  1%|          | 1378/153499 [01:15<2:37:36, 16.09it/s]

  1%|          | 1381/153499 [01:15<2:19:59, 18.11it/s]

  1%|          | 1385/153499 [01:16<1:58:42, 21.36it/s]

  1%|          | 1388/153499 [01:16<3:15:24, 12.97it/s]

  1%|          | 1391/153499 [01:16<2:59:53, 14.09it/s]

  1%|          | 1393/153499 [0

  1%|          | 1784/153499 [01:36<2:02:37, 20.62it/s]

  1%|          | 1788/153499 [01:37<1:47:38, 23.49it/s]

  1%|          | 1791/153499 [01:37<1:58:20, 21.37it/s]

  1%|          | 1794/153499 [01:37<2:16:41, 18.50it/s]

  1%|          | 1797/153499 [01:37<2:26:45, 17.23it/s]

  1%|          | 1799/153499 [01:37<2:26:43, 17.23it/s]

  1%|          | 1803/153499 [01:37<2:02:36, 20.62it/s]

  1%|          | 1806/153499 [01:37<1:52:52, 22.40it/s]

  1%|          | 1809/153499 [01:38<2:08:19, 19.70it/s]

  1%|          | 1812/153499 [01:38<2:52:14, 14.68it/s]

  1%|          | 1815/153499 [01:38<2:27:37, 17.13it/s]

  1%|          | 1818/153499 [01:38<2:19:59, 18.06it/s]

  1%|          | 1821/153499 [01:38<2:46:14, 15.21it/s]

  1%|          | 1823/153499 [01:39<3:03:06, 13.81it/s]

  1%|          | 1826/153499 [01:39<2:41:32, 15.65it/s]

  1%|          | 1829/153499 [01:39<2:29:59, 16.85it/s]

  1%|          | 1833/153499 [01:39<2:04:31, 20.30it/s]

  1%|          | 1836/153499 [0

...

 98%|█████████▊| 150972/153499 [2:34:27<01:37, 25.96it/s]

 98%|█████████▊| 150978/153499 [2:34:27<01:20, 31.18it/s]

 98%|█████████▊| 150982/153499 [2:34:28<01:28, 28.35it/s]

 98%|█████████▊| 150986/153499 [2:34:28<01:22, 30.29it/s]

 98%|█████████▊| 150990/153499 [2:34:28<01:40, 24.96it/s]

 98%|█████████▊| 150994/153499 [2:34:28<01:33, 26.83it/s]

 98%|█████████▊| 150998/153499 [2:34:28<01:25, 29.38it/s]

 98%|█████████▊| 151002/153499 [2:34:28<01:20, 30.89it/s]

 98%|█████████▊| 151006/153499 [2:34:29<01:50, 22.59it/s]

 98%|█████████▊| 151009/153499 [2:34:29<02:39, 15.65it/s]

 98%|█████████▊| 151015/153499 [2:34:29<02:06, 19.70it/s]

 98%|█████████▊| 151019/153499 [2:34:29<02:08, 19.30it/s]

 98%|█████████▊| 151024/153499 [2:34:29<01:56, 21.16it/s]

 98%|█████████▊| 151027/153499 [2:34:30<01:54, 21.56it/s]

 98%|█████████▊| 151031/153499 [2:34:30<01:48, 22.84it/s]

 98%|█████████▊| 151036/153499 [2:34:30<01:33, 26.33it/s]

 98%|█████████▊| 151040/153499 [2:34:30<01:27, 28.10it/s

 99%|█████████▊| 151505/153499 [2:34:49<01:27, 22.83it/s]

 99%|█████████▊| 151510/153499 [2:34:49<01:16, 26.04it/s]

 99%|█████████▊| 151513/153499 [2:34:50<01:15, 26.26it/s]

 99%|█████████▊| 151516/153499 [2:34:50<01:31, 21.67it/s]

 99%|█████████▊| 151519/153499 [2:34:50<01:28, 22.47it/s]

 99%|█████████▊| 151523/153499 [2:34:50<01:16, 25.87it/s]

 99%|█████████▊| 151528/153499 [2:34:50<01:08, 28.88it/s]

 99%|█████████▊| 151532/153499 [2:34:50<01:14, 26.34it/s]

 99%|█████████▊| 151537/153499 [2:34:51<01:26, 22.65it/s]

 99%|█████████▊| 151540/153499 [2:34:51<01:36, 20.32it/s]

 99%|█████████▊| 151545/153499 [2:34:51<01:20, 24.29it/s]

 99%|█████████▊| 151548/153499 [2:34:51<01:29, 21.78it/s]

 99%|█████████▊| 151553/153499 [2:34:51<01:20, 24.03it/s]

 99%|█████████▊| 151557/153499 [2:34:51<01:18, 24.81it/s]

 99%|█████████▊| 151560/153499 [2:34:52<01:33, 20.65it/s]

 99%|█████████▊| 151563/153499 [2:34:52<01:35, 20.37it/s]

 99%|█████████▊| 151569/153499 [2:34:52<01:24, 22.95it/s

 99%|█████████▉| 152057/153499 [2:35:10<01:00, 23.80it/s]

 99%|█████████▉| 152060/153499 [2:35:11<00:59, 24.15it/s]

 99%|█████████▉| 152065/153499 [2:35:11<00:52, 27.32it/s]

 99%|█████████▉| 152070/153499 [2:35:11<00:48, 29.55it/s]

 99%|█████████▉| 152075/153499 [2:35:11<00:44, 32.12it/s]

 99%|█████████▉| 152079/153499 [2:35:11<00:48, 29.14it/s]

 99%|█████████▉| 152083/153499 [2:35:11<00:51, 27.76it/s]

 99%|█████████▉| 152089/153499 [2:35:11<00:49, 28.64it/s]

 99%|█████████▉| 152093/153499 [2:35:12<00:54, 25.84it/s]

 99%|█████████▉| 152096/153499 [2:35:12<00:52, 26.68it/s]

 99%|█████████▉| 152099/153499 [2:35:12<00:57, 24.31it/s]

 99%|█████████▉| 152102/153499 [2:35:12<00:56, 24.69it/s]

 99%|█████████▉| 152105/153499 [2:35:12<01:06, 20.90it/s]

 99%|█████████▉| 152108/153499 [2:35:12<01:07, 20.58it/s]

 99%|█████████▉| 152111/153499 [2:35:13<01:09, 19.95it/s]

 99%|█████████▉| 152114/153499 [2:35:13<01:05, 21.02it/s]

 99%|█████████▉| 152118/153499 [2:35:13<00:56, 24.46it/s

 99%|█████████▉| 152629/153499 [2:35:31<00:31, 27.22it/s]

 99%|█████████▉| 152635/153499 [2:35:31<00:27, 31.93it/s]

 99%|█████████▉| 152640/153499 [2:35:31<00:24, 35.66it/s]

 99%|█████████▉| 152644/153499 [2:35:31<00:24, 34.65it/s]

 99%|█████████▉| 152648/153499 [2:35:31<00:26, 31.80it/s]

 99%|█████████▉| 152652/153499 [2:35:31<00:25, 32.96it/s]

 99%|█████████▉| 152657/153499 [2:35:32<00:23, 36.23it/s]

 99%|█████████▉| 152661/153499 [2:35:32<00:39, 21.08it/s]

 99%|█████████▉| 152665/153499 [2:35:32<00:37, 22.45it/s]

 99%|█████████▉| 152668/153499 [2:35:32<00:34, 24.11it/s]

 99%|█████████▉| 152672/153499 [2:35:32<00:31, 26.50it/s]

 99%|█████████▉| 152676/153499 [2:35:33<00:35, 22.86it/s]

 99%|█████████▉| 152679/153499 [2:35:33<00:35, 23.30it/s]

 99%|█████████▉| 152682/153499 [2:35:33<00:33, 24.42it/s]

 99%|█████████▉| 152685/153499 [2:35:33<00:36, 22.14it/s]

 99%|█████████▉| 152690/153499 [2:35:33<00:30, 26.17it/s]

 99%|█████████▉| 152694/153499 [2:35:33<00:27, 29.01it/s

100%|█████████▉| 153253/153499 [2:35:51<00:05, 44.20it/s]

100%|█████████▉| 153259/153499 [2:35:52<00:05, 43.41it/s]

100%|█████████▉| 153265/153499 [2:35:52<00:05, 44.10it/s]

100%|█████████▉| 153273/153499 [2:35:52<00:04, 47.34it/s]

100%|█████████▉| 153278/153499 [2:35:52<00:05, 38.63it/s]

100%|█████████▉| 153285/153499 [2:35:52<00:04, 44.21it/s]

100%|█████████▉| 153290/153499 [2:35:52<00:04, 43.41it/s]

100%|█████████▉| 153295/153499 [2:35:52<00:04, 41.38it/s]

100%|█████████▉| 153302/153499 [2:35:53<00:04, 41.32it/s]

100%|█████████▉| 153307/153499 [2:35:53<00:04, 42.92it/s]

100%|█████████▉| 153312/153499 [2:35:53<00:04, 43.76it/s]

100%|█████████▉| 153318/153499 [2:35:53<00:03, 46.85it/s]

100%|█████████▉| 153323/153499 [2:35:53<00:06, 26.88it/s]

100%|█████████▉| 153327/153499 [2:35:53<00:07, 24.36it/s]

100%|█████████▉| 153331/153499 [2:35:54<00:06, 26.14it/s]

100%|█████████▉| 153336/153499 [2:35:54<00:05, 30.51it/s]

100%|█████████▉| 153340/153499 [2:35:54<00:05, 28.31it/s

In [46]:
reviews_df.to_csv('after_lemma_noun.csv')

In [47]:
reviews_df.head()

author     bank_license        bank_name            city  \
0       uhnov1  лицензия № 2562          Бинбанк       г. Москва   
1       Foryou  лицензия № 1481  Сбербанк России  г. Новосибирск   
2   Vladimir84  лицензия № 2562          Бинбанк       г. Москва   
3       643609  лицензия № 1481  Сбербанк России   г. Ставрополь   
4  anfisa-2003  лицензия № 2766         ОТП Банк    г. Челябинск   

              datetime  num_comments  rating_grade  rating_not_checked  \
0  2015-06-08 12:50:54             0           NaN               False   
1  2015-06-08 11:09:57             0           NaN               False   
2  2015-06-05 20:14:28             1           NaN               False   
3  2015-06-05 13:51:01             2           NaN               False   
4  2015-06-05 10:58:12             1           NaN               False   

                                                text  \
0  добрый день являться клиент банка поручитель к...   
1  добрый день являться держатель зарплатный карт...   
2  здравствовать дублировать свой заявление можай...   
3  добрый день открыть расчётный счёт сбербанк юр...   
4  год взять кредит ваш банка заявить я сумма том...   

                                               title  \
0                                             Жалоба   
1      Не могу пользоваться услугой Сбербанк он-лайн   
2                    Двойное списание за один товар.   
3  Меняют проценты комиссии  не предупредив и не ...   
4             Верните денежные средства за страховку   

                                           text_noun  
0  день клиент банка поручитель договор лицо отно...  
1  день держатель карта сбербанк россия год фамил...  
2  заявление карта покупка интернет магазин сумма...  
3  день счёт сбербанк юр лицо договор комиссия пе...  
4  год кредит банка сумма рубль год менеджер срок...

In [55]:
for i in the_most_common_words(reviews_df,'text_noun').most_common(10):
    print(i)

('банка', 399725)
('карта', 334999)
('банк', 268864)
('это', 209775)
('деньга', 179819)
('день', 170152)
('год', 169247)
('кредит', 156177)
('мой', 156140)
('который', 149017)


### 4. Постройте кривые Ципфа и Хипса

In [ ]:
all_reviews[1]

### 5. Ответьте на следующие вопросы:
   * какое слово встречается чаще, "сотрудник" или "клиент"?
   * сколько раз встречается слова "мошенничество" и "доверие"?


### 6. В поле "rating_grade" записана оценка отзыва по шкале от 1 до 5. Используйте меру $tf-idf$, для того, чтобы найти ключевые слова и биграмы для положительных отзывов (с оценкой 5) и отрицательных отзывов (с оценкой 1)

## Часть 2. Тематическое моделирование [20/100]

1. Постройте несколько тематических моделей коллекции документов с разным числом тем. Приведите примеры понятных (интерпретируемых) тем.
2. Найдите темы, в которых упомянуты конкретные банки (Сбербанк, ВТБ, другой банк). Можете ли вы их прокомментировать / объяснить?

Эта часть задания может быть сделана с использованием gensim. 

## Часть 3. Классификация текстов [40/100]

Сформулируем для простоты задачу бинарной классификации: будем классифицировать на два класса, то есть, различать резко отрицательные отзывы (с оценкой 1) и положительные отзывы (с оценкой 5). 

1.  Составьте обучающее и тестовое множество: выберите из всего набора данных N1 отзывов с оценкой 1 и N2 отзывов с оценкой 5 (значение N1 и N2 – на ваше усмотрение). Используйте ```sklearn.model_selection.train_test_split``` для разделения множества отобранных документов на обучающее и тестовое. 
2. Используйте любой известный вам алгоритм классификации текстов для решения задачи и получите baseline. Сравните разные варианты векторизации текста: использование только униграм, пар или троек слов или с использованием символьных $n$-грам. 
3. Сравните, как изменяется качество решения задачи при использовании скрытых тем в качестве признаков:
* 1-ый вариант: $tf-idf$ преобразование (```sklearn.feature_extraction.text.TfidfTransformer```) и сингулярное разложение (оно же – латентый семантический анализ) (```sklearn.decomposition.TruncatedSVD```), 
* 2-ой вариант: тематические модели LDA (```sklearn.decomposition.LatentDirichletAllocation```). 

Используйте accuracy и F-measure для оценки качества классификации. 

Ниже написан примерный Pipeline для классификации текстов. 

Эта часть задания может быть сделана с использованием sklearn. 

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier

# !!! На каждом этапе Pipeline нужно указать свои параметры
# 1-ый вариант: tf-idf + LSI
# 2-ой вариант: LDA

# clf = Pipeline([
#     ('vect', CountVectorizer(analyzer = 'char', ngram_range={4,6})),
#     ('clf', RandomForestClassifier()),
# ])



clf = Pipeline([ 
    ('vect', CountVectorizer()), 
    ('tfidf', TfidfTransformer()), 
    ('tm', TruncatedSVD()), 
    ('clf', RandomForestClassifier())
])
